In [1]:
#api for extracting the results from wikidata

#https://www.wikidata.org/w/api.php?search=las&language=en&uselang=en&format=jsonfm&limit=25&action=wbsearchentities

# importing modules 
import requests 
from lxml import etree 
import wikipedia
import sys
import re
import pickle
import numpy as np
import os
import sys
import pandas as pd
import seaborn as sns
import matplotlib as plt
from tensorflow import keras
from nltk.corpus import stopwords 
from nltk.corpus import wordnet,words
# Ignore warnings
import warnings
warnings.filterwarnings('ignore')


pd.set_option('display.max_columns', None)
np.set_printoptions(threshold=sys.maxsize)
np.set_printoptions(precision=3)
sns.set(style="darkgrid")
plt.rcParams['axes.labelsize'] = 14
plt.rcParams['xtick.labelsize'] = 12
plt.rcParams['ytick.labelsize'] = 12


max_words = 50
tokenize = keras.preprocessing.text.Tokenizer(num_words=max_words, char_level=False)



C:\Users\Varadharajan R\AppData\Local\Programs\Python\Python37\lib\site-packages\tensorflow\python\framework\dtypes.py:516: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
C:\Users\Varadharajan R\AppData\Local\Programs\Python\Python37\lib\site-packages\tensorflow\python\framework\dtypes.py:517: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
C:\Users\Varadharajan R\AppData\Local\Programs\Python\Python37\lib\site-packages\tensorflow\python\framework\dtypes.py:518: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int1

In [3]:
#loading species names from the csv

df = pd.read_csv("C:/Users/Varadharajan R/Desktop/FYP/pyscripts/species_dataset.csv")

col_names =  ['species', 'words']
train_text  = pd.DataFrame(columns = col_names)
                      
# iterating over rows using iterrows() function  
species = []
for i, j in df.iterrows(): 
    species.append(j[0]) 

    
for specimen in species:
    SEARCHPAGE = specimen
    if SEARCHPAGE == "Magnolia_soulangeana" :
       SEARCHPAGE = "Magnolia_×_soulangeana" 
    page=wikipedia.WikipediaPage(SEARCHPAGE)
    content=page.content
    content_list=content.split('.')
    train_text= train_text.append(pd.DataFrame({'species':SEARCHPAGE,'words':content_list}),ignore_index=True)
    
print(train_text)
#print("###################################   TRAINING DATASET DESCRIPTION  ###############################################################")
print(train_text.describe())



              species                                              words
0      Abies concolor  Abies concolor, the white fir, is a coniferous...
1      Abies concolor   This tree is native to the mountains of weste...
2      Abies concolor   White fir live over 300-years and naturally o...
3      Abies concolor  It is popular as an ornamental landscaping tre...
4      Abies concolor  \nThe specific epithet concolor means "all one...
...               ...                                                ...
14259     Ulmus rubra            fulva\n"Herbarium specimen - E00824847"
14260     Ulmus rubra                                Herbarium Catalogue
14261     Ulmus rubra                     Royal Botanic Garden Edinburgh
14262     Ulmus rubra                               Sheet described as U
14263     Ulmus rubra       fulva, RBGE specimen from Späth nursery 1902

[14264 rows x 2 columns]
                species  words
count             14264  14264
unique              185  12854
top  

In [4]:
train_text.to_csv('%s_%s_train.csv' % ("backup", "data"), index=False)


In [85]:
train_df = train_text
train_df

species                                              words
0      Abies concolor  Abies concolor, the white fir, is a coniferous...
1      Abies concolor   This tree is native to the mountains of weste...
2      Abies concolor   White fir live over 300-years and naturally o...
3      Abies concolor  It is popular as an ornamental landscaping tre...
4      Abies concolor  \nThe specific epithet concolor means "all one...
...               ...                                                ...
14259     Ulmus rubra            fulva\n"Herbarium specimen - E00824847"
14260     Ulmus rubra                                Herbarium Catalogue
14261     Ulmus rubra                     Royal Botanic Garden Edinburgh
14262     Ulmus rubra                               Sheet described as U
14263     Ulmus rubra       fulva, RBGE specimen from Späth nursery 1902

[14264 rows x 2 columns]

In [86]:
from nltk import pos_tag
from nltk.corpus import stopwords
import spacy
import en_core_web_sm

sp = en_core_web_sm.load()
stop_words = set(stopwords.words('english'))

cols = ['species','sentence','Named Entities','Question Words','Answers','Questions']
named_train = pd.DataFrame(columns = cols)

for i, j in train_df.iterrows():
    species = j[0]
    sentence= j[1]
    sentence = re.sub(r"[^a-zA-Z0-9]+", ' ', sentence)
    tokenized_sentence=sentence.split(' ')
    #print(tokenized_sentence)
    #print(pos_tag([i for i in tokenized_sentence if i]))
    pos_tagged_sentence=pos_tag([i for i in tokenized_sentence if i])
    sen = sp(sentence)
    #print(sen.ents) #Named Entities
    #Named_Entities = list(sen.ents)
    named_entities = [(word,pos) for (word, pos) in pos_tagged_sentence if (pos=="NN") or (pos=="JJ") or (pos=="VB") or (pos=="NNS") or (pos=="VBZ") or (pos=="JJS") or (pos=="NNP") or (pos=="JJR") or (pos=="RB") or (pos=="RBS") or (pos=="RBR") or(pos=="RP") or(pos=="CD") and word not in stop_words]
    
    #print(named_entities)
    named_train= named_train.append(pd.DataFrame({'species':species,'sentence':sentence,'Named Entities':named_entities}),ignore_index=True)
#[pos_tag(sent) for sent in sentences]

In [87]:
named_train

Answers    Named Entities Question Words Questions  \
0          NaN      (Abies, NNS)            NaN       NaN   
1          NaN       (white, JJ)            NaN       NaN   
2          NaN         (fir, NN)            NaN       NaN   
3          NaN         (is, VBZ)            NaN       NaN   
4          NaN  (coniferous, JJ)            NaN       NaN   
...        ...               ...            ...       ...   
132653     NaN   (specimen, NNS)            NaN       NaN   
132654     NaN         (Sp, NNP)            NaN       NaN   
132655     NaN          (th, NN)            NaN       NaN   
132656     NaN     (nursery, NN)            NaN       NaN   
132657     NaN        (1902, CD)            NaN       NaN   

                                                 sentence         species  
0       Abies concolor the white fir is a coniferous t...  Abies concolor  
1       Abies concolor the white fir is a coniferous t...  Abies concolor  
2       Abies concolor the white fir is a coniferous t...  Abies concolor  
3       Abies concolor the white fir is a coniferous t...  Abies concolor  
4       Abies concolor the white fir is a coniferous t...  Abies concolor  
...                                                   ...             ...  
132653        fulva RBGE specimen from Sp th nursery 1902     Ulmus rubra  
132654        fulva RBGE specimen from Sp th nursery 1902     Ulmus rubra  
132655        fulva RBGE specimen from Sp th nursery 1902     Ulmus rubra  
132656        fulva RBGE specimen from Sp th nursery 1902     Ulmus rubra  
132657        fulva RBGE specimen from Sp th nursery 1902     Ulmus rubra  

[132658 rows x 6 columns]

In [88]:
#question types what,where,which,who,whose,why,how,when 

#what or how is for action performed --verb
#RP OR PARTICLE is how
# which is for object -- comparative or superlative word
#why is reasoning -- because can be used

#CD == time or number or date then the question is when or how many
#who,whose is Proper noun -- noun
#where is for place - noun

for i, j in named_train['Named Entities'].iteritems():
    word,tag=j
    #print(word,tag)
    if tag == "NN" or tag == "NNS" or tag == "NNP" or tag =="JJ" or tag=="JJS" or tag=="JJR" :
       question_words=['which','who','whose','where','what']
    elif tag=="VB" or tag=="VBZ" or tag=="RB" or tag=="RBR" or tag=="RBP" :
        question_words=['what','how']
    elif tag=="RP":
        question_words=['how']
    elif tag=="CD":
        question_words=['how many','when']
        
    #print(word,tag,question_words)
    #print(i)
    named_train['Question Words'].iloc[i]=question_words
    named_train['Answers'].iloc[i]=word
#word,tag=named_train['Named Entities']

In [89]:
named_train

Answers    Named Entities                    Question Words  \
0            Abies      (Abies, NNS)  [which, who, whose, where, what]   
1            white       (white, JJ)  [which, who, whose, where, what]   
2              fir         (fir, NN)  [which, who, whose, where, what]   
3               is         (is, VBZ)                       [what, how]   
4       coniferous  (coniferous, JJ)  [which, who, whose, where, what]   
...            ...               ...                               ...   
132653    specimen   (specimen, NNS)  [which, who, whose, where, what]   
132654          Sp         (Sp, NNP)  [which, who, whose, where, what]   
132655          th          (th, NN)  [which, who, whose, where, what]   
132656     nursery     (nursery, NN)  [which, who, whose, where, what]   
132657        1902        (1902, CD)                  [how many, when]   

       Questions                                           sentence  \
0            NaN  Abies concolor the white fir is a coniferous t...   
1            NaN  Abies concolor the white fir is a coniferous t...   
2            NaN  Abies concolor the white fir is a coniferous t...   
3            NaN  Abies concolor the white fir is a coniferous t...   
4            NaN  Abies concolor the white fir is a coniferous t...   
...          ...                                                ...   
132653       NaN        fulva RBGE specimen from Sp th nursery 1902   
132654       NaN        fulva RBGE specimen from Sp th nursery 1902   
132655       NaN        fulva RBGE specimen from Sp th nursery 1902   
132656       NaN        fulva RBGE specimen from Sp th nursery 1902   
132657       NaN        fulva RBGE specimen from Sp th nursery 1902   

               species  
0       Abies concolor  
1       Abies concolor  
2       Abies concolor  
3       Abies concolor  
4       Abies concolor  
...                ...  
132653     Ulmus rubra  
132654     Ulmus rubra  
132655     Ulmus rubra  
132656     Ulmus rubra  
132657     Ulmus rubra  

[132658 rows x 6 columns]

In [90]:
named_train.to_csv('%s_%s_train.csv' % ("backup_question", "data"), index=False)


In [1]:
import nltk
from nameparser.parser import HumanName
from nltk.corpus import wordnet
from nltk import word_tokenize,pos_tag,ne_chunk

person_list = []
person_names=person_list
def get_human_names(text):
    tokens = word_tokenize(text)
    pos = pos_tag(tokens)
    sentt = ne_chunk(pos, binary = False)

    person = []
    name = ""
    for subtree in sentt.subtrees(filter=lambda t: t.label() == 'PERSON'):
        for leaf in subtree.leaves():
            person.append(leaf[0])
        if len(person) > 1: #avoid grabbing lone surnames
            for part in person:
                name += part + ' '
            if name[:-1] not in person_list:
                person_list.append(name[:-1])
            name = ''
        person = []
#     print (person_list)


In [3]:
from geotext import GeoText
from dateparser.search import search_dates

for i,j in named_train.iterrows():
    answers=j[0]
    question_words=j[2]
    sentence=j[4]
    species_name=j[5]
    questions=[]
    try:
        places = GeoText(sentence)
        cities=places.cities
        for country in places.countries : 
            cities.append(country)
    
        dates = search_dates(sentence)
        if dates is None:
            dates=[]
        names = get_human_names(sentence)
        for person in person_list:
            person_split = person.split(" ")
            for name in person_split:
                if wordnet.synsets(name):
                    if(name in person):
                        person_names.remove(person)
                        break
        list_of_words = sentence.split()
        next_word = list_of_words[list_of_words.index('because') + 1]
        next_word.append(list_of_words[list_of_words.index('because') + 2])
        next_word.append(list_of_words[list_of_words.index('because') - 1])
        next_word.append(list_of_words[list_of_words.index('because') - 2])
    except:
        pass
        next_word=[]
    
    
    #if species_name is the word then what is the question easily
    if answers in species_name :
       question_words=['what']
       for question_word in question_words:
           moded_sentence=sentence.replace(species_name,'') 
           #print(question_word+' '+moded_sentence+' ?')
           questions.append(question_word+' '+moded_sentence+' ?') 
    #location find and replace the question word with where
    elif answers in cities :
       question_words=['Where','Which place'] 
       for city in cities:
           #print(city)
           moded_sentence=sentence.replace(city,'')
           for question_word in question_words:
               #print(question_word+' '+moded_sentence+' ?')
               questions.append(question_word+' '+moded_sentence+' ?') 
    #person name find and replace with who or whose
    elif len(person_names) and answers in person_names :
       print(person_names) 
       question_words=['Who','Whose'] 
       for person in person_names :
           moded_sentence=sentence.replace(person,'')
           for question_word in question_words:
               #print(question_word+' '+moded_sentence+' ?')
               questions.append(question_word+' '+moded_sentence+' ?') 
        
    #date find and replace with when
    elif len(dates) and answers in dates :
       question_words=['When'] 
       for date in dates:
           moded_sentence=sentence.replace(date[0],'') 
           #print(question_word+' '+moded_sentence+' ?')
           questions.append(question_word+' '+moded_sentence+' ?')
        
    #if not a date but number replace with how many
    elif answers.isnumeric() :
       question_words=['How many'] 
       for question_word in question_words:
           moded_sentence=sentence.replace(answers,'') 
           #print(question_word+' '+moded_sentence+' ?')
           questions.append(question_word+' '+moded_sentence+' ?')
    #if there is a because immediate to the answer replace with why or how
    elif answers in next_word :
        question_words = ['How','Why']
        for question_word in question_words:
            moded_sentence=sentence.replace(answers,'') 
            #print(question_word+' '+moded_sentence+' ?')
            questions.append(question_word+' '+moded_sentence+' ?')
    #no such cases
    elif answers in sentence:
       temp=question_words.replace("[","").replace("]","").replace("'","")
       question_words=temp.split(',')
       print(question_words)
       for question_word in question_words:
           moded_sentence=sentence.replace(answers,'')
#            print(question_word+' '+moded_sentence+' ?') 
           questions.append(question_word+' '+moded_sentence+' ?')
    
    print(i)
    named_train['Questions'].iloc[i]=questions


0
['which', ' who', ' whose', ' where', ' what']
1


C:\Users\Varadharajan R\AppData\Local\Programs\Python\Python37\lib\site-packages\pandas\core\indexing.py:205: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer(indexer, value)


['which', ' who', ' whose', ' where', ' what']
2
['what', ' how']
3
['which', ' who', ' whose', ' where', ' what']
4
['which', ' who', ' whose', ' where', ' what']
5
['which', ' who', ' whose', ' where', ' what']
6
['which', ' who', ' whose', ' where', ' what']
7
['which', ' who', ' whose', ' where', ' what']
8
['which', ' who', ' whose', ' where', ' what']
9
['what', ' how']
10
['which', ' who', ' whose', ' where', ' what']
11
['which', ' who', ' whose', ' where', ' what']
12
['which', ' who', ' whose', ' where', ' what']
13
['which', ' who', ' whose', ' where', ' what']
14
['which', ' who', ' whose', ' where', ' what']
15
['which', ' who', ' whose', ' where', ' what']
16
['which', ' who', ' whose', ' where', ' what']
17
['which', ' who', ' whose', ' where', ' what']
18
19
['which', ' who', ' whose', ' where', ' what']
20
['which', ' who', ' whose', ' where', ' what']
21
['which', ' who', ' whose', ' where', ' what']
22
['which', ' who', ' whose', ' where', ' what']
23
['which', ' who

['which', ' who', ' whose', ' where', ' what']
243
['which', ' who', ' whose', ' where', ' what']
244
['what', ' how']
245
['which', ' who', ' whose', ' where', ' what']
246
['which', ' who', ' whose', ' where', ' what']
247
['which', ' who', ' whose', ' where', ' what']
248
['what', ' how']
249
['which', ' who', ' whose', ' where', ' what']
250
['how many', ' when']
251
['which', ' who', ' whose', ' where', ' what']
252
['which', ' who', ' whose', ' where', ' what']
253
['which', ' who', ' whose', ' where', ' what']
254
['which', ' who', ' whose', ' where', ' what']
255
['which', ' who', ' whose', ' where', ' what']
256
['which', ' who', ' whose', ' where', ' what']
257
['which', ' who', ' whose', ' where', ' what']
258
['which', ' who', ' whose', ' where', ' what']
259
['which', ' who', ' whose', ' where', ' what']
260
['what', ' how']
261
['which', ' who', ' whose', ' where', ' what']
262
['which', ' who', ' whose', ' where', ' what']
263
264
265
['which', ' who', ' whose', ' where'

482
483
['which', ' who', ' whose', ' where', ' what']
484
485
486
['what', ' how']
487
['what', ' how']
488
['which', ' who', ' whose', ' where', ' what']
489
['which', ' who', ' whose', ' where', ' what']
490
['which', ' who', ' whose', ' where', ' what']
491
['which', ' who', ' whose', ' where', ' what']
492
['which', ' who', ' whose', ' where', ' what']
493
['which', ' who', ' whose', ' where', ' what']
494
['which', ' who', ' whose', ' where', ' what']
495
['which', ' who', ' whose', ' where', ' what']
496
['how']
497
498
['which', ' who', ' whose', ' where', ' what']
499
500
['which', ' who', ' whose', ' where', ' what']
501
['which', ' who', ' whose', ' where', ' what']
502
['which', ' who', ' whose', ' where', ' what']
503
['which', ' who', ' whose', ' where', ' what']
504
['which', ' who', ' whose', ' where', ' what']
505
['what', ' how']
506
['what', ' how']
507
['which', ' who', ' whose', ' where', ' what']
508
['which', ' who', ' whose', ' where', ' what']
509
['which', ' w

...

['which', ' who', ' whose', ' where', ' what']
131835
['which', ' who', ' whose', ' where', ' what']
131836
['what', ' how']
131837
['what', ' how']
131838
['which', ' who', ' whose', ' where', ' what']
131839
131840
['which', ' who', ' whose', ' where', ' what']
131841
['which', ' who', ' whose', ' where', ' what']
131842
['which', ' who', ' whose', ' where', ' what']
131843
['which', ' who', ' whose', ' where', ' what']
131844
['which', ' who', ' whose', ' where', ' what']
131845
131846
['what', ' how']
131847
['what', ' how']
131848
['what', ' how']
131849
['which', ' who', ' whose', ' where', ' what']
131850
['which', ' who', ' whose', ' where', ' what']
131851
['which', ' who', ' whose', ' where', ' what']
131852
['which', ' who', ' whose', ' where', ' what']
131853
['which', ' who', ' whose', ' where', ' what']
131854
['which', ' who', ' whose', ' where', ' what']
131855
['what', ' how']
131856
['which', ' who', ' whose', ' where', ' what']
131857
['which', ' who', ' whose', ' wh

['which', ' who', ' whose', ' where', ' what']
132039
['which', ' who', ' whose', ' where', ' what']
132040
['which', ' who', ' whose', ' where', ' what']
132041
['which', ' who', ' whose', ' where', ' what']
132042
['which', ' who', ' whose', ' where', ' what']
132043
['what', ' how']
132044
['what', ' how']
132045
['which', ' who', ' whose', ' where', ' what']
132046
['which', ' who', ' whose', ' where', ' what']
132047
['which', ' who', ' whose', ' where', ' what']
132048
['which', ' who', ' whose', ' where', ' what']
132049
['what', ' how']
132050
['how many', ' when']
132051
['which', ' who', ' whose', ' where', ' what']
132052
['which', ' who', ' whose', ' where', ' what']
132053
['which', ' who', ' whose', ' where', ' what']
132054
['which', ' who', ' whose', ' where', ' what']
132055
['which', ' who', ' whose', ' where', ' what']
132056
['which', ' who', ' whose', ' where', ' what']
132057
['what', ' how']
132058
132059
132060
132061
['which', ' who', ' whose', ' where', ' what

['what', ' how']
132245
['which', ' who', ' whose', ' where', ' what']
132246
['which', ' who', ' whose', ' where', ' what']
132247
['what', ' how']
132248
['what', ' how']
132249
['what', ' how']
132250
['which', ' who', ' whose', ' where', ' what']
132251
['which', ' who', ' whose', ' where', ' what']
132252
['which', ' who', ' whose', ' where', ' what']
132253
132254
['which', ' who', ' whose', ' where', ' what']
132255
['which', ' who', ' whose', ' where', ' what']
132256
132257
['which', ' who', ' whose', ' where', ' what']
132258
['which', ' who', ' whose', ' where', ' what']
132259
['which', ' who', ' whose', ' where', ' what']
132260
['which', ' who', ' whose', ' where', ' what']
132261
['which', ' who', ' whose', ' where', ' what']
132262
['which', ' who', ' whose', ' where', ' what']
132263
['which', ' who', ' whose', ' where', ' what']
132264
['which', ' who', ' whose', ' where', ' what']
132265
['which', ' who', ' whose', ' where', ' what']
132266
['which', ' who', ' whose'

['which', ' who', ' whose', ' where', ' what']
132429
['which', ' who', ' whose', ' where', ' what']
132430
['which', ' who', ' whose', ' where', ' what']
132431
['which', ' who', ' whose', ' where', ' what']
132432
['which', ' who', ' whose', ' where', ' what']
132433
['which', ' who', ' whose', ' where', ' what']
132434
132435
132436
132437
132438
['which', ' who', ' whose', ' where', ' what']
132439
['which', ' who', ' whose', ' where', ' what']
132440
['which', ' who', ' whose', ' where', ' what']
132441
['which', ' who', ' whose', ' where', ' what']
132442
['which', ' who', ' whose', ' where', ' what']
132443
['which', ' who', ' whose', ' where', ' what']
132444
132445
['which', ' who', ' whose', ' where', ' what']
132446
['which', ' who', ' whose', ' where', ' what']
132447
['which', ' who', ' whose', ' where', ' what']
132448
['which', ' who', ' whose', ' where', ' what']
132449
['which', ' who', ' whose', ' where', ' what']
132450
['which', ' who', ' whose', ' where', ' what']


['which', ' who', ' whose', ' where', ' what']
132610
132611
['which', ' who', ' whose', ' where', ' what']
132612
['which', ' who', ' whose', ' where', ' what']
132613
132614
132615
['which', ' who', ' whose', ' where', ' what']
132616
['which', ' who', ' whose', ' where', ' what']
132617
['which', ' who', ' whose', ' where', ' what']
132618
['which', ' who', ' whose', ' where', ' what']
132619
['which', ' who', ' whose', ' where', ' what']
132620
['which', ' who', ' whose', ' where', ' what']
132621
['which', ' who', ' whose', ' where', ' what']
132622
['which', ' who', ' whose', ' where', ' what']
132623
132624
132625
['which', ' who', ' whose', ' where', ' what']
132626
['which', ' who', ' whose', ' where', ' what']
132627
['which', ' who', ' whose', ' where', ' what']
132628
['which', ' who', ' whose', ' where', ' what']
132629
['which', ' who', ' whose', ' where', ' what']
132630
['which', ' who', ' whose', ' where', ' what']
132631
['which', ' who', ' whose', ' where', ' what']


In [4]:
named_train
named_train.to_csv('%s_%s_train.csv' % ("all_questions_final", "data"), index=False)


In [5]:
named_train

Answers        Named Entities  \
0            Abies      ('Abies', 'NNS')   
1            white       ('white', 'JJ')   
2              fir         ('fir', 'NN')   
3               is         ('is', 'VBZ')   
4       coniferous  ('coniferous', 'JJ')   
...            ...                   ...   
132653    specimen   ('specimen', 'NNS')   
132654          Sp         ('Sp', 'NNP')   
132655          th          ('th', 'NN')   
132656     nursery     ('nursery', 'NN')   
132657        1902        ('1902', 'CD')   

                                    Question Words  \
0       ['which', 'who', 'whose', 'where', 'what']   
1       ['which', 'who', 'whose', 'where', 'what']   
2       ['which', 'who', 'whose', 'where', 'what']   
3                                  ['what', 'how']   
4       ['which', 'who', 'whose', 'where', 'what']   
...                                            ...   
132653  ['which', 'who', 'whose', 'where', 'what']   
132654  ['which', 'who', 'whose', 'where', 'what']   
132655  ['which', 'who', 'whose', 'where', 'what']   
132656  ['which', 'who', 'whose', 'where', 'what']   
132657                        ['how many', 'when']   

                                                Questions  \
0       [what  the white fir is a coniferous tree in t...   
1       [which Abies concolor the  fir is a coniferous...   
2       [which Abies concolor the white  is a conifero...   
3       [what Abies concolor the white fir  a conifero...   
4       [which Abies concolor the white fir is a  tree...   
...                                                   ...   
132653  [which  fulva RBGE  from Sp th nursery 1902 ?,...   
132654  [which  fulva RBGE specimen from  th nursery 1...   
132655  [which  fulva RBGE specimen from Sp  nursery 1...   
132656  [which  fulva RBGE specimen from Sp th  1902 ?...   
132657  [How many  fulva RBGE specimen from Sp th nurs...   

                                                 sentence         species  
0       Abies concolor the white fir is a coniferous t...  Abies concolor  
1       Abies concolor the white fir is a coniferous t...  Abies concolor  
2       Abies concolor the white fir is a coniferous t...  Abies concolor  
3       Abies concolor the white fir is a coniferous t...  Abies concolor  
4       Abies concolor the white fir is a coniferous t...  Abies concolor  
...                                                   ...             ...  
132653        fulva RBGE specimen from Sp th nursery 1902     Ulmus rubra  
132654        fulva RBGE specimen from Sp th nursery 1902     Ulmus rubra  
132655        fulva RBGE specimen from Sp th nursery 1902     Ulmus rubra  
132656        fulva RBGE specimen from Sp th nursery 1902     Ulmus rubra  
132657        fulva RBGE specimen from Sp th nursery 1902     Ulmus rubra  

[132658 rows x 6 columns]

In [2]:
import pandas as pd
named_train = pd.read_csv("C:/Users/Varadharajan R/Desktop/FYP/pyscripts/backup_question_data_train.csv")

In [95]:
#QUESTION ANSWERING MODEL for the clozed QA dataset

import keras
from keras.models import Sequential, Model
from keras.layers.embeddings import Embedding
from keras.layers import Input, Activation, Dense, Permute, Dropout
from keras.layers import concatenate,add,dot
from keras.layers import LSTM, GRU
from keras.utils.data_utils import get_file
from keras.preprocessing.sequence import pad_sequences
from keras import backend as K

import time
from functools import reduce
import tarfile
import numpy as np
import re

train_epochs = 100
batch_size = 32
lstm_size = 64

def tokenize(sent):
    print(sent)
    return [ x.strip() for x in sent.split(' ')]

def parse_stories(lines, only_supporting=False):
    '''Parse stories provided in the bAbi tasks format
    If only_supporting is true, only the sentences
    that support the answer are kept.
    '''
    data = []
    story = []
    for line in lines:
        line = line.decode('utf8').strip()
        nid, line = line.split(' ',1)
        nid = int(nid)
        if nid == 1:
            story = []
        if '\t' in line:
            q, a, supporting = line.split('\t')
            q = tokenize(q)
            substory = None
            if only_supporting:
                # Only select the related substory
                supporting = map(int, supporting.split())
                substory = [story[i - 1] for i in supporting]
            else:
                # Provide all the substories
                substory = [x for x in story if x]
            data.append((substory, q, a))
            story.append('')
        else:
            sent = tokenize(line)
            story.append(sent)
    return data


def vectorize_stories(data, word_idx, story_maxlen, query_maxlen):
    X = []
    Xq = []
    Y = []
    for story, query, answer in data:
        x = [word_idx[w] for w in story]
        xq = [word_idx[w] for w in query]
        # let's not forget that index 0 is reserved
        y = np.zeros(len(word_idx) + 1)
        y[word_idx[answer]] = 1
        X.append(x)
        Xq.append(xq)
        Y.append(y)
    return (pad_sequences(X, maxlen=story_maxlen),
            pad_sequences(Xq, maxlen=query_maxlen), np.array(Y))


specii= named_train['species'].unique()
specii = [x for x in specii  if x!= 'Abies concolor' and x!='Abies nordmanniana' and x!='Acer campestre' and x!='Acer ginnala' and x!='Acer griseum' and x!='Acer palmatum']


for species_name in specii:
    stories = [(j[4].split(' '), items.split(' '), j[0]) for i,j in named_train.iterrows() for items in j[3] if j[5] ==species_name]
#     print('Extracting train and test datasets:')

    i=0
    train_stories=[]
    test_stories=[]
    for x in stories :
    #     print(x)
        if i <= round(len(stories)*0.66666) :
            train_stories.append(x) 
        else :
            test_stories.append(x)
        i=i+1


    vocab = set()
    for story, q, answer in train_stories + test_stories:
        vocab |= set(story + q + [answer])
    vocab = sorted(vocab)

    # Reserve 0 for masking via pad_sequences
    vocab_size = len(vocab) + 1
    story_maxlen = max(map(len, (x for x, _, _ in train_stories + test_stories)))
    query_maxlen = max(map(len, (x for _, x, _ in train_stories + test_stories)))

    print('---------------------------------'+species_name+'-------------------------------------------')
    print('Vocab size:', vocab_size, 'unique words')
    print('Story max length:', story_maxlen, 'words')
    print('Query max length:', query_maxlen, 'words')
    print('Number of training stories:', len(train_stories))
    print('Number of test stories:', len(test_stories))
    print('-')
    print('Here\'s what a "story" tuple looks like (input, query, answer):')
    print(train_stories[0])
    print('-')
    print('Vectorizing the word sequences...')

    word_idx = dict((c, i + 1) for i, c in enumerate(vocab))
    idx_word = dict((i+1, c) for i,c in enumerate(vocab))
    inputs_train, queries_train, answers_train = vectorize_stories(train_stories,
                                                               word_idx,
                                                               story_maxlen,
                                                               query_maxlen)
    inputs_test, queries_test, answers_test = vectorize_stories(test_stories,
                                                            word_idx,
                                                            story_maxlen,
                                                            query_maxlen)
#     print('-')
#     print('inputs: integer tensor of shape (samples, max_length)')
#     print('inputs_train shape:', inputs_train.shape)
#     print('inputs_test shape:', inputs_test.shape)
#     print('-')
#     print('queries: integer tensor of shape (samples, max_length)')
#     print('queries_train shape:', queries_train.shape)
#     print('queries_test shape:', queries_test.shape)
#     print('-')
#     print('answers: binary (1 or 0) tensor of shape (samples, vocab_size)')
#     print('answers_train shape:', answers_train.shape)
#     print('answers_test shape:', answers_test.shape)
#     print('-')
    print('Compiling...')

    # placeholders
    input_sequence = Input((story_maxlen,))
    question = Input((query_maxlen,))

#     print('Input sequence:', input_sequence)
#     print('Question:', question)

    # encoders
    # embed the input sequence into a sequence of vectors
    input_encoder_m = Sequential()
    input_encoder_m.add(Embedding(input_dim=vocab_size,
                              output_dim=64))
    input_encoder_m.add(Dropout(0.3))
    # output: (samples, story_maxlen, embedding_dim)

    # embed the input into a sequence of vectors of size query_maxlen
    input_encoder_c = Sequential()
    input_encoder_c.add(Embedding(input_dim=vocab_size,
                              output_dim=query_maxlen))
    input_encoder_c.add(Dropout(0.3))
    # output: (samples, story_maxlen, query_maxlen)

    # embed the question into a sequence of vectors
    question_encoder = Sequential()
    question_encoder.add(Embedding(input_dim=vocab_size,
                               output_dim=64,
                               input_length=query_maxlen))
    question_encoder.add(Dropout(0.3))
    # output: (samples, query_maxlen, embedding_dim)

    # encode input sequence and questions (which are indices)
    # to sequences of dense vectors
    input_encoded_m = input_encoder_m(input_sequence)
#     print('Input encoded m', input_encoded_m)
    input_encoded_c = input_encoder_c(input_sequence)
#     print('Input encoded c', input_encoded_c)
    question_encoded = question_encoder(question)
#     print('Question encoded', question_encoded)


    # compute a 'match' between the first input vector sequence
    # and the question vector sequence
    # shape: `(samples, story_maxlen, query_maxlen)
#     print("--------------------------------------")
    #match = merge([input_encoded_m, question_encoded],mode='dot',dot_axes=[2,2])
    match = dot([input_encoded_m,question_encoded],axes=2, normalize=False)
    match = Activation('softmax')(match)
#     print('Match shape', match)

    # add the match matrix with the second input vector sequence
    response = add([match, input_encoded_c])  # (samples, story_maxlen, query_maxlen)
    response = Permute((2, 1))(response)  # (samples, query_maxlen, story_maxlen)
#     print('Response shape', response)

    # concatenate the response vector with the question vector sequence
    answer = concatenate([response, question_encoded])
#     print('Answer shape', answer)

    answer = LSTM(lstm_size)(answer)  # Generate tensors of shape 32
    answer = Dropout(0.3)(answer)
    answer = Dense(vocab_size)(answer)  # (samples, vocab_size)
    # we output a probability distribution over the vocabulary
    answer = Activation('softmax')(answer)

    # build the final model
    model = Model([input_sequence, question], answer)
    model.compile(optimizer='adam', loss='categorical_crossentropy',
              metrics=['accuracy'])

#     print("-------------Model Summary------------")
#     print(model.summary())

    # train, batch_size = 32 and epochs = 120
    print("Training the model")
    model.fit([inputs_train, queries_train], answers_train, batch_size, train_epochs,
      validation_data=([inputs_test, queries_test], answers_test))
    model.save(species_name+'.h5')
    print("Saving the model")
    time.sleep(100)


---------------------------------Acer platanoides-------------------------------------------
Vocab size: 732 unique words
Story max length: 56 words
Query max length: 59 words
Number of training stories: 2744
Number of test stories: 1371
-
Here's what a "story" tuple looks like (input, query, answer):
(['Acer', 'platanoides', 'the', 'Norway', 'maple', 'is', 'a', 'species', 'of', 'maple', 'native', 'to', 'eastern', 'and', 'central', 'Europe', 'and', 'western', 'Asia', 'from', 'France', 'east', 'to', 'Russia', 'north', 'to', 'southern', 'Scandinavia', 'and', 'southeast', 'to', 'northern', 'Iran'], ['what', '', 'the', 'Norway', 'maple', 'is', 'a', 'species', 'of', 'maple', 'native', 'to', 'eastern', 'and', 'central', 'Europe', 'and', 'western', 'Asia', 'from', 'France', 'east', 'to', 'Russia', 'north', 'to', 'southern', 'Scandinavia', 'and', 'southeast', 'to', 'northern', 'Iran', '?'], 'Acer')
-
Vectorizing the word sequences...
Compiling...
Training the model
Train on 2744 samples, valid

5458/5458 [==============================] - 9s 2ms/step - loss: 5.7577 - acc: 0.0299 - val_loss: 10.2893 - val_acc: 0.0198
Epoch 6/100
5458/5458 [==============================] - 8s 2ms/step - loss: 5.2854 - acc: 0.0515 - val_loss: 10.0096 - val_acc: 0.0249
Epoch 7/100
5458/5458 [==============================] - 8s 2ms/step - loss: 4.7965 - acc: 0.0808 - val_loss: 10.3942 - val_acc: 0.0088
Epoch 8/100
5458/5458 [==============================] - 9s 2ms/step - loss: 4.3435 - acc: 0.1097 - val_loss: 10.6424 - val_acc: 0.0139
Epoch 9/100
5458/5458 [==============================] - 9s 2ms/step - loss: 3.9882 - acc: 0.1284 - val_loss: 11.1834 - val_acc: 0.0059
Epoch 10/100
5458/5458 [==============================] - 8s 2ms/step - loss: 3.6780 - acc: 0.1568 - val_loss: 10.6865 - val_acc: 0.0062
Epoch 11/100
5458/5458 [==============================] - 8s 2ms/step - loss: 3.4423 - acc: 0.1717 - val_loss: 11.1368 - val_acc: 0.0077
Epoch 12/100
5458/5458 [==============================] - 

7400/7400 [==============================] - 17s 2ms/step - loss: 2.7287 - acc: 0.2978 - val_loss: 11.1373 - val_acc: 0.0216
Epoch 18/100
7400/7400 [==============================] - 17s 2ms/step - loss: 2.6143 - acc: 0.3204 - val_loss: 11.2261 - val_acc: 0.0211
Epoch 19/100
7400/7400 [==============================] - 17s 2ms/step - loss: 2.5253 - acc: 0.3341 - val_loss: 11.3909 - val_acc: 0.0249
Epoch 20/100
7400/7400 [==============================] - 17s 2ms/step - loss: 2.4403 - acc: 0.3489 - val_loss: 11.4571 - val_acc: 0.0251
Epoch 21/100
7400/7400 [==============================] - 17s 2ms/step - loss: 2.3404 - acc: 0.3666 - val_loss: 11.4814 - val_acc: 0.0214
Epoch 22/100
7400/7400 [==============================] - 17s 2ms/step - loss: 2.2884 - acc: 0.3782 - val_loss: 11.5257 - val_acc: 0.0279
Epoch 23/100
7400/7400 [==============================] - 17s 2ms/step - loss: 2.1908 - acc: 0.4082 - val_loss: 11.5988 - val_acc: 0.0292
Epoch 24/100
7400/7400 [=======================

2021/2021 [==============================] - 3s 2ms/step - loss: 2.7769 - acc: 0.2474 - val_loss: 10.7862 - val_acc: 0.0297
Epoch 28/100
2021/2021 [==============================] - 3s 2ms/step - loss: 2.7142 - acc: 0.2499 - val_loss: 10.9928 - val_acc: 0.0268
Epoch 29/100
2021/2021 [==============================] - 3s 2ms/step - loss: 2.6670 - acc: 0.2533 - val_loss: 10.7864 - val_acc: 0.0278
Epoch 30/100
2021/2021 [==============================] - 3s 2ms/step - loss: 2.6119 - acc: 0.2632 - val_loss: 10.9761 - val_acc: 0.0119
Epoch 31/100
2021/2021 [==============================] - 3s 2ms/step - loss: 2.5851 - acc: 0.2632 - val_loss: 11.1758 - val_acc: 0.0119
Epoch 32/100
2021/2021 [==============================] - 3s 2ms/step - loss: 2.5325 - acc: 0.2667 - val_loss: 11.3507 - val_acc: 0.0119
Epoch 33/100
2021/2021 [==============================] - 3s 2ms/step - loss: 2.4874 - acc: 0.2830 - val_loss: 11.1357 - val_acc: 0.0287 2s - lo
Epoch 34/100
2021/2021 [======================

Epoch 87/100
2021/2021 [==============================] - 3s 2ms/step - loss: 1.2239 - acc: 0.6141 - val_loss: 12.2123 - val_acc: 0.0238
Epoch 88/100
2021/2021 [==============================] - 3s 2ms/step - loss: 1.2009 - acc: 0.6338 - val_loss: 12.1492 - val_acc: 0.0258
Epoch 89/100
2021/2021 [==============================] - 3s 2ms/step - loss: 1.1745 - acc: 0.6309 - val_loss: 12.1963 - val_acc: 0.0258
Epoch 90/100
2021/2021 [==============================] - 3s 2ms/step - loss: 1.1557 - acc: 0.6348 - val_loss: 12.1206 - val_acc: 0.0268
Epoch 91/100
2021/2021 [==============================] - 3s 2ms/step - loss: 1.1575 - acc: 0.6432 - val_loss: 12.1500 - val_acc: 0.0208
Epoch 92/100
2021/2021 [==============================] - 3s 2ms/step - loss: 1.1444 - acc: 0.6353 - val_loss: 12.2983 - val_acc: 0.0238
Epoch 93/100
2021/2021 [==============================] - 3s 2ms/step - loss: 1.1077 - acc: 0.6522 - val_loss: 12.3542 - val_acc: 0.0238
Epoch 94/100
2021/2021 [=================

...

836/836 [==============================] - 11s 13ms/step - loss: 3.0389 - acc: 0.1280 - val_loss: 9.9430 - val_acc: 0.0000e+00
Epoch 31/100
836/836 [==============================] - 11s 13ms/step - loss: 3.0163 - acc: 0.1232 - val_loss: 9.8577 - val_acc: 0.0000e+00
Epoch 32/100
836/836 [==============================] - 11s 13ms/step - loss: 2.9564 - acc: 0.1459 - val_loss: 10.0264 - val_acc: 0.0000e+00
Epoch 33/100
836/836 [==============================] - 11s 13ms/step - loss: 2.9588 - acc: 0.1459 - val_loss: 9.9269 - val_acc: 0.0000e+00
Epoch 34/100
836/836 [==============================] - 11s 13ms/step - loss: 2.9409 - acc: 0.1364 - val_loss: 9.8818 - val_acc: 0.0000e+00
Epoch 35/100
836/836 [==============================] - 11s 13ms/step - loss: 2.8854 - acc: 0.1483 - val_loss: 10.0950 - val_acc: 0.0000e+00
Epoch 36/100
836/836 [==============================] - 11s 13ms/step - loss: 2.8998 - acc: 0.1459 - val_loss: 9.5258 - val_acc: 0.0000e+00
Epoch 37/100
836/836 [=========

Epoch 89/100
836/836 [==============================] - 11s 13ms/step - loss: 2.0213 - acc: 0.3660 - val_loss: 10.9466 - val_acc: 0.0024
Epoch 90/100
836/836 [==============================] - 11s 13ms/step - loss: 2.0609 - acc: 0.3648 - val_loss: 10.6504 - val_acc: 0.0024
Epoch 91/100
836/836 [==============================] - 11s 13ms/step - loss: 2.2701 - acc: 0.3134 - val_loss: 10.0443 - val_acc: 0.0000e+00
Epoch 92/100
836/836 [==============================] - 11s 13ms/step - loss: 2.2178 - acc: 0.3074 - val_loss: 10.4324 - val_acc: 0.0000e+00
Epoch 93/100
836/836 [==============================] - 11s 13ms/step - loss: 2.0883 - acc: 0.3266 - val_loss: 10.4951 - val_acc: 0.0000e+00
Epoch 94/100
836/836 [==============================] - 11s 13ms/step - loss: 2.0180 - acc: 0.3732 - val_loss: 10.7321 - val_acc: 0.0024
Epoch 95/100
836/836 [==============================] - 11s 13ms/step - loss: 2.0950 - acc: 0.3337 - val_loss: 10.5642 - val_acc: 0.0000e+00
Epoch 96/100
836/836 [===

Epoch 43/100
1280/1280 [==============================] - 13s 10ms/step - loss: 1.9336 - acc: 0.3914 - val_loss: 11.3608 - val_acc: 0.0485
Epoch 44/100
1280/1280 [==============================] - 13s 10ms/step - loss: 1.8986 - acc: 0.4156 - val_loss: 11.3638 - val_acc: 0.0329
Epoch 45/100
1280/1280 [==============================] - 13s 10ms/step - loss: 1.8835 - acc: 0.4148 - val_loss: 11.3141 - val_acc: 0.0407
Epoch 46/100
1280/1280 [==============================] - 13s 10ms/step - loss: 1.8437 - acc: 0.4305 - val_loss: 11.3210 - val_acc: 0.0485
Epoch 47/100
1280/1280 [==============================] - 13s 10ms/step - loss: 1.8252 - acc: 0.4320 - val_loss: 11.3575 - val_acc: 0.0329
Epoch 48/100
1280/1280 [==============================] - 13s 10ms/step - loss: 1.7898 - acc: 0.4359 - val_loss: 11.4991 - val_acc: 0.0391
Epoch 49/100
1280/1280 [==============================] - 13s 10ms/step - loss: 1.7597 - acc: 0.4578 - val_loss: 11.3689 - val_acc: 0.0313
Epoch 50/100
1280/1280 [===

Training the model
Train on 5336 samples, validate on 2666 samples
Epoch 1/100
5336/5336 [==============================] - 202s 38ms/step - loss: 6.3858 - acc: 0.0298 - val_loss: 8.0569 - val_acc: 0.0319
Epoch 2/100
5336/5336 [==============================] - 188s 35ms/step - loss: 5.9376 - acc: 0.0350 - val_loss: 8.7171 - val_acc: 0.0169
Epoch 3/100
5336/5336 [==============================] - 188s 35ms/step - loss: 5.8234 - acc: 0.0373 - val_loss: 9.2074 - val_acc: 0.0360
Epoch 4/100
5336/5336 [==============================] - 188s 35ms/step - loss: 5.6736 - acc: 0.0433 - val_loss: 8.9374 - val_acc: 0.0229
Epoch 5/100
5336/5336 [==============================] - 188s 35ms/step - loss: 5.4435 - acc: 0.0508 - val_loss: 9.6474 - val_acc: 0.0338
Epoch 6/100
5336/5336 [==============================] - 188s 35ms/step - loss: 5.1225 - acc: 0.0663 - val_loss: 9.8208 - val_acc: 0.0289
Epoch 7/100
5336/5336 [==============================] - 188s 35ms/step - loss: 4.7744 - acc: 0.0819 - va

KeyboardInterrupt: 